# 2D heat equation

From the tutorial
+ https://docs.sciml.ai/MethodOfLines/stable/tutorials/heatss/
+ https://docs.sciml.ai/MethodOfLines/stable/tutorials/heat/

Using `MethodOfLines.jl` (https://github.com/SciML/MethodOfLines.jl/) to symbolically define the PDE system and use the [finite difference method](https://en.wikipedia.org/wiki/Finite_difference_method) (FDM) to solve the following PDE:

$$
\frac{\partial u}{\partial t} = \frac{\partial^2 u}{\partial x^2} + \frac{\partial^2 u}{\partial y^2}
$$

In [1]:
using ModelingToolkit
using MethodOfLines
using DomainSets
using OrdinaryDiffEq
using Plots

[ Info: Precompiling IJuliaExt [2f4121a4-3b3a-5ce6-9c5e-1f2673ce168a]


Setup variables and differential operators

In [2]:
@variables t x y
@variables u(..)

Dt = Differential(t)
Dxx = Differential(x)^2
Dyy = Differential(y)^2

Differential(y) ∘ Differential(y)

PDE equation

In [3]:
eq = Dt(u(t, x, y)) ~ Dxx(u(t, x, y)) + Dyy(u(t, x, y))

Differential(t)(u(t, x, y)) ~ Differential(x)(Differential(x)(u(t, x, y))) + Differential(y)(Differential(y)(u(t, x, y)))

Boundary conditions

In [4]:
bcs = [
    u(0, x, y) ~ 0,
    u(t, 0, y) ~ x * y,
    u(t, 1, y) ~ x * y,
    u(t, x, 0) ~ x * y,
    u(t, x, 1) ~ x * y,
]

5-element Vector{Equation}:
 u(0, x, y) ~ 0
 u(t, 0, y) ~ x*y
 u(t, 1, y) ~ x*y
 u(t, x, 0) ~ x*y
 u(t, x, 1) ~ x*y

Space and time domains

In [5]:
domains = [
    t ∈ Interval(0.0, 1.0),
    x ∈ Interval(0.0, 1.0),
    y ∈ Interval(0.0, 1.0)
]

3-element Vector{Symbolics.VarDomainPairing}:
 Symbolics.VarDomainPairing(t, 0.0 .. 1.0)
 Symbolics.VarDomainPairing(x, 0.0 .. 1.0)
 Symbolics.VarDomainPairing(y, 0.0 .. 1.0)

PDE system

In [6]:
@named pdesys = PDESystem(eq, bcs, domains, [t, x, y], [u(t, x, y)])

PDESystem
Equations: Equation[Differential(t)(u(t, x, y)) ~ Differential(x)(Differential(x)(u(t, x, y))) + Differential(y)(Differential(y)(u(t, x, y)))]
Boundary Conditions: Equation[u(0, x, y) ~ 0, u(t, 0, y) ~ x*y, u(t, 1, y) ~ x*y, u(t, x, 0) ~ x*y, u(t, x, 1) ~ x*y]
Domain: Symbolics.VarDomainPairing[Symbolics.VarDomainPairing(t, 0.0 .. 1.0), Symbolics.VarDomainPairing(x, 0.0 .. 1.0), Symbolics.VarDomainPairing(y, 0.0 .. 1.0)]
Dependent Variables: Num[u(t, x, y)]
Independent Variables: Num[t, x, y]
Parameters: SciMLBase.NullParameters()
Default Parameter ValuesDict{Any, Any}()

discretize the PDE system

In [7]:
N = 20
discretization = MOLFiniteDifference([x=>N, y=>N], t, approx_order=2, grid_align=MethodOfLines.EdgeAlignedGrid())
prob = discretize(pdesys, discretization)

ODEProblem with uType Vector{Float64} and tType Float64. In-place: true
timespan: (0.0, 1.0)
u0: 400-element Vector{Float64}:
 -0.0
 -0.0
 -0.0
 -0.0
 -0.0
 -0.0
 -0.0
 -0.0
 -0.0
 -0.0
 -0.0
 -0.0
 -0.0
  ⋮
 -0.0
 -0.0
 -0.0
 -0.0
 -0.0
 -0.0
 -0.0
 -0.0
 -0.0
 -0.0
 -0.0
 -0.0

Solve the PDE

In [8]:
sol = solve(prob, KenCarp4(), saveat=0.01)

retcode: Success
Interpolation: Dict{Num, Interpolations.GriddedInterpolation{Float64, 3, Array{Float64, 3}, Interpolations.Gridded{Interpolations.Linear{Interpolations.Throw{Interpolations.OnGrid}}}, Tuple{Vector{Float64}, Vector{Float64}, Vector{Float64}}}}
t: 101-element Vector{Float64}:
 0.0
 0.01
 0.02
 0.03
 0.04
 0.05
 0.06
 0.07
 0.08
 0.09
 0.1
 0.11
 0.12
 ⋮
 0.89
 0.9
 0.91
 0.92
 0.93
 0.94
 0.95
 0.96
 0.97
 0.98
 0.99
 1.0ivs: 3-element Vector{SymbolicUtils.BasicSymbolic{Real}}:
 t
 x
 ydomain:([0.0, 0.01, 0.02, 0.03, 0.04, 0.05, 0.06, 0.07, 0.08, 0.09  …  0.91, 0.92, 0.93, 0.94, 0.95, 0.96, 0.97, 0.98, 0.99, 1.0], -0.025:0.05:1.025, -0.025:0.05:1.025)
u: Dict{Num, Array{Float64, 3}} with 1 entry:
  u(t, x, y) => [0.0 0.0 … 0.0 0.0; 0.0 1.6849e-10 … -0.0214844 0.0; … ; 0.0 -0…

Extract data

In [9]:
discrete_x = sol[x]
discrete_y = sol[y]
discrete_t = sol[t]
solu = sol[u(t, x, y)]

101×22×22 Array{Float64, 3}:
[:, :, 1] =
 0.0   0.0           0.0          …   0.0         0.0        0.0
 0.0   1.6849e-10    5.24652e-10     -0.0148733  -0.0214844  0.0
 0.0  -9.69678e-8   -3.62435e-7      -0.0176809  -0.0225107  0.0
 0.0  -2.79302e-6   -9.19576e-6      -0.0189859  -0.0229673  0.0
 0.0  -1.59429e-5   -5.04371e-5      -0.0198141  -0.023254   0.0
 0.0  -4.46441e-5   -0.000138676  …  -0.0204107  -0.0234577  0.0
 0.0  -8.88607e-5   -0.00027295      -0.0208908  -0.0236212  0.0
 0.0  -0.000142968  -0.0004361       -0.0212853  -0.023755   0.0
 0.0  -0.000201733  -0.000612571     -0.0216081  -0.0238641  0.0
 0.0  -0.000260136  -0.000787453     -0.0218747  -0.0239541  0.0
 0.0  -0.000313856  -0.000947999  …  -0.0220977  -0.0240293  0.0
 0.0  -0.000361957  -0.00109159      -0.0222817  -0.0240914  0.0
 0.0  -0.000404475  -0.00121839      -0.0224324  -0.0241421  0.0
 ⋮                                ⋱               ⋮          
 0.0  -0.000624994  -0.00187498      -0.023125   -0.

Animate the solution

In [10]:
anim = @animate for k in eachindex(discrete_t)
    heatmap(solu[k, 2:end-1, 2:end-1], title="u @ t=$(discrete_t[k])", aspect_ratio=:equal)
end

mp4(anim,"2Dheat.mp4", fps = 8)

[ Info: Saved animation to /tmp/docs/pde/2Dheat.mp4


Plots.AnimatedGif("/tmp/docs/pde/2Dheat.mp4")

## Runtime environment

In [11]:
using Pkg
Pkg.status()

Status `/tmp/docs/pde/Project.toml`
⌅ [5b8099bc] DomainSets v0.6.7
  [94925ecb] MethodOfLines v0.11.0
  [961ee093] ModelingToolkit v9.15.0
  [8913a72c] NonlinearSolve v3.12.4
  [1dea7af3] OrdinaryDiffEq v6.80.1
  [91a5bcdd] Plots v1.40.4
Info Packages marked with ⌅ have new versions available but compatibility constraints restrict them from upgrading. To see why use `status --outdated`


In [12]:
using InteractiveUtils
InteractiveUtils.versioninfo()

Julia Version 1.10.3
Commit 0b4590a5507 (2024-04-30 10:59 UTC)
Build Info:
  Official https://julialang.org/ release
Platform Info:
  OS: Linux (x86_64-linux-gnu)
  CPU: 4 × AMD EPYC 7763 64-Core Processor
  WORD_SIZE: 64
  LIBM: libopenlibm
  LLVM: libLLVM-15.0.7 (ORCJIT, znver3)
Threads: 4 default, 0 interactive, 2 GC (on 4 virtual cores)
Environment:
  JULIA_CI = true
  JULIA_NUM_THREADS = auto
  JULIA_CONDAPKG_BACKEND = Null
  JULIA_PATH = /usr/local/julia/
  JULIA_DEPOT_PATH = /srv/juliapkg/
